In [10]:
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [11]:
import os
import sys
from pathlib import Path

# check if workding_dir is in local variables
if "workding_dir" not in locals():
    workding_dir = str(Path.cwd().parent)

os.chdir(workding_dir)
sys.path.append(workding_dir)
print("workding dir:", workding_dir)

workding dir: /Users/inflaton/code/engd/papers/rapget-translation


In [12]:
from dotenv import find_dotenv, load_dotenv

found_dotenv = find_dotenv(".env")

if len(found_dotenv) == 0:
    found_dotenv = find_dotenv(".env.example")
print(f"loading env vars from: {found_dotenv}")
load_dotenv(found_dotenv, override=True)

loading env vars from: /Users/inflaton/code/engd/papers/rapget-translation/.env


True

In [13]:
import os

model_name = os.getenv("MODEL_NAME")
adapter_name_or_path = os.getenv("ADAPTER_NAME_OR_PATH")
load_in_4bit = os.getenv("LOAD_IN_4BIT") == "true"
data_path = os.getenv("DATA_PATH")
results_path = "results/mac-results_greedy_decoding.csv"  # os.getenv("RESULTS_PATH")
use_english_datasets = os.getenv("USE_ENGLISH_DATASETS") == "true"

print(model_name, adapter_name_or_path, load_in_4bit, data_path, results_path)

Qwen/Qwen2-7B-Instruct None False datasets/mac/mac.tsv results/mac-results_greedy_decoding.csv


In [14]:
%%time
os.environ["TOKENIZERS_PARALLELISM"] = "true"

!python --version
!pip show torch transformers

Python 3.11.9
Name: torch
Version: 2.4.0
Summary: Tensors and Dynamic neural networks in Python with strong GPU acceleration
Home-page: https://pytorch.org/
Author: PyTorch Team
Author-email: packages@pytorch.org
License: BSD-3
Location: /Users/inflaton/anaconda3/envs/rapget/lib/python3.11/site-packages
Requires: filelock, fsspec, jinja2, networkx, sympy, typing-extensions
Required-by: accelerate, peft, torchaudio, torchvision
---
Name: transformers
Version: 4.43.3
Summary: State-of-the-art Machine Learning for JAX, PyTorch and TensorFlow
Home-page: https://github.com/huggingface/transformers
Author: The Hugging Face team (past and future) with the help of all our contributors (https://github.com/huggingface/transformers/graphs/contributors)
Author-email: transformers@huggingface.co
License: Apache 2.0 License
Location: /Users/inflaton/anaconda3/envs/rapget/lib/python3.11/site-packages
Requires: filelock, huggingface-hub, numpy, packaging, pyyaml, regex, requests, safetensors, tokenize

In [15]:
from llm_toolkit.llm_utils import *
from llm_toolkit.translation_utils import *

device = check_gpu()

MPS is available


In [16]:
import pandas as pd

df = pd.read_csv(results_path)
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1133 entries, 0 to 1132
Data columns (total 25 columns):
 #   Column                                           Non-Null Count  Dtype 
---  ------                                           --------------  ----- 
 0   chinese                                          1133 non-null   object
 1   english                                          1133 non-null   object
 2   Qwen/Qwen2-7B-Instruct/rpp-1.00                  1133 non-null   object
 3   Qwen/Qwen2-7B-Instruct/rpp-1.02                  1133 non-null   object
 4   Qwen/Qwen2-7B-Instruct/rpp-1.04                  1133 non-null   object
 5   Qwen/Qwen2-7B-Instruct/rpp-1.06                  1133 non-null   object
 6   Qwen/Qwen2-7B-Instruct/rpp-1.08                  1133 non-null   object
 7   Qwen/Qwen2-7B-Instruct/rpp-1.10                  1133 non-null   object
 8   Qwen/Qwen2-7B-Instruct/rpp-1.12                  1133 non-null   object
 9   Qwen/Qwen2-7B-Instruct/rpp-1.14          

In [18]:
metrics_df = get_metrics(df)
metrics_df

Qwen/Qwen2-7B-Instruct/rpp-1.00: {'meteor': 0.3757937058055942, 'bleu_scores': {'bleu': 0.11257687997946404, 'precisions': [0.4221057489451477, 0.15152552819915763, 0.07046669041681511, 0.03563738956121464], 'brevity_penalty': 1.0, 'length_ratio': 1.004836038423319, 'translation_length': 30336, 'reference_length': 30190}, 'rouge_scores': {'rouge1': 0.42398582083049496, 'rouge2': 0.17397502646147225, 'rougeL': 0.364447549509206, 'rougeLsum': 0.36430686603130313}, 'accuracy': 0.00088261253309797, 'correct_ids': [364]}
Qwen/Qwen2-7B-Instruct/rpp-1.02: {'meteor': 0.3768162203335968, 'bleu_scores': {'bleu': 0.11553860771639841, 'precisions': [0.421923611570795, 0.15446511467968776, 0.07288535852297123, 0.03751491646778043], 'brevity_penalty': 1.0, 'length_ratio': 1.0007949652202717, 'translation_length': 30214, 'reference_length': 30190}, 'rouge_scores': {'rouge1': 0.42716298071770475, 'rouge2': 0.17952709653204155, 'rougeL': 0.3693774755784234, 'rougeLsum': 0.3693387884292203}, 'accuracy':

model   rpp    meteor    bleu_1  \
0                   Qwen/Qwen2-7B-Instruct  1.00  0.375794  0.112577   
1                   Qwen/Qwen2-7B-Instruct  1.02  0.376816  0.115539   
2                   Qwen/Qwen2-7B-Instruct  1.04  0.371515  0.113116   
3                   Qwen/Qwen2-7B-Instruct  1.06  0.372161  0.109860   
4                   Qwen/Qwen2-7B-Instruct  1.08  0.371297  0.108095   
5                   Qwen/Qwen2-7B-Instruct  1.10  0.371353  0.108097   
6                   Qwen/Qwen2-7B-Instruct  1.12  0.368204  0.105056   
7                   Qwen/Qwen2-7B-Instruct  1.14  0.363077  0.100516   
8                   Qwen/Qwen2-7B-Instruct  1.16  0.360604  0.095724   
9                   Qwen/Qwen2-7B-Instruct  1.18  0.360785  0.095713   
10                  Qwen/Qwen2-7B-Instruct  1.20  0.356755  0.091249   
11                  Qwen/Qwen2-7B-Instruct  1.22  0.351004  0.083507   
12                  Qwen/Qwen2-7B-Instruct  1.24  0.346560  0.079543   
13                  Qwen/Qwen2-7B-Instruct  1.26  0.343517  0.078588   
14                  Qwen/Qwen2-7B-Instruct  1.28  0.340534  0.072038   
15                  Qwen/Qwen2-7B-Instruct  1.30  0.334469  0.062148   
16         internlm/internlm2_5-7b-chat-1m  1.00  0.371535  0.105977   
17         internlm/internlm2_5-7b-chat-1m  1.02  0.352901  0.086979   
18                 Qwen/Qwen2-72B-Instruct  1.00  0.394969  0.122949   
19  shenzhi-wang/Llama3.1-70B-Chinese-Chat  1.00  0.381686  0.115183   
20  shenzhi-wang/Llama3.1-70B-Chinese-Chat  1.02  0.381085  0.114341   
21  shenzhi-wang/Llama3.1-70B-Chinese-Chat  1.04  0.380191  0.113532   
22  shenzhi-wang/Llama3.1-70B-Chinese-Chat  1.06  0.378622  0.112205   

     rouge_l  ews_score  repetition_score  total_repetitions  \
0   0.364448   0.000000          0.000000           0.000000   
1   0.369377   0.000000          0.000000           0.000000   
2   0.363507   0.000000          0.000000           0.000000   
3   0.360978   0.000000          0.000000           0.000000   
4   0.359519   0.000000          0.000000           0.000000   
5   0.359491   0.000000          0.000000           0.000000   
6   0.358827   0.000000          0.000000           0.000000   
7   0.349651   0.000000          0.000000           0.000000   
8   0.350555   0.000000          0.000000           0.000000   
9   0.344145   0.000000          0.000000           0.000000   
10  0.344555   0.000000          0.000000           0.000000   
11  0.336948   0.000000          0.000000           0.000000   
12  0.333417   0.000000          0.000000           0.000000   
13  0.330136   0.000000          0.000000           0.000000   
14  0.325964   0.000000          0.000000           0.000000   
15  0.321984   0.005296          0.005296           0.005296   
16  0.363161   0.000000          0.000000           0.000000   
17  0.339714   0.000000          0.000000           0.000000   
18  0.383994   0.000000          0.000000           0.000000   
19  0.370474   0.000000          0.000000           0.000000   
20  0.369741   0.000000          0.000000           0.000000   
21  0.369297   0.000000          0.000000           0.000000   
22  0.368737   0.000000          0.000000           0.000000   

    num_entries_with_max_output_tokens  
0                                    0  
1                                    0  
2                                    0  
3                                    0  
4                                    0  
5                                    0  
6                                    0  
7                                    0  
8                                    0  
9                                    0  
10                                   0  
11                                   0  
12                                   0  
13                                   0  
14                                   0  
15                                   1  
16                                   0  
17                               

In [19]:
tokenizers = {
    model: load_tokenizer(model) for model in metrics_df["model"].unique()
}

In [20]:
col = "Qwen/Qwen2-7B-Instruct/rpp-1.30"
df[["ews_score", "repetition_score", "total_repetitions"]] = df[col].apply(
    detect_scores
)
df["output_tokens"] = df[col].apply(
    lambda x: len(tokenizers[col.split("/rpp")[0]](x)["input_ids"])
)


In [21]:
rows = df.query("ews_score > 0")
rows

chinese     english Qwen/Qwen2-7B-Instruct/rpp-1.00  \
531   14.分娩  Childbirth                       14. Labor   

    Qwen/Qwen2-7B-Instruct/rpp-1.02 Qwen/Qwen2-7B-Instruct/rpp-1.04  \
531                  14. Childbirth                  14. Childbirth   

    Qwen/Qwen2-7B-Instruct/rpp-1.06 Qwen/Qwen2-7B-Instruct/rpp-1.08  \
531                       14. Labor                       14. Labor   

    Qwen/Qwen2-7B-Instruct/rpp-1.10 Qwen/Qwen2-7B-Instruct/rpp-1.12  \
531                       14. Labor                  14. Childbirth   

    Qwen/Qwen2-7B-Instruct/rpp-1.14  ...  \
531                  14. Childbirth  ...   

              internlm/internlm2_5-7b-chat-1m/rpp-1.02  \
531  Translation: Delivery\n\nThe word "分娩" is a co...   

    Qwen/Qwen2-72B-Instruct/rpp-1.00  \
531                   14. Childbirth   

    shenzhi-wang/Llama3.1-70B-Chinese-Chat/rpp-1.00  \
531                                      Childbirth   

    shenzhi-wang/Llama3.1-70B-Chinese-Chat/rpp-1.02  \
531                                      Childbirth   

    shenzhi-wang/Llama3.1-70B-Chinese-Chat/rpp-1.04  \
531                                      Childbirth   

    shenzhi-wang/Llama3.1-70B-Chinese-Chat/rpp-1.06 ews_score  \
531                                      Childbirth         6   

    repetition_score total_repetitions output_tokens  
531               42                48          2048  

[1 rows x 29 columns]

In [22]:
row = rows.iloc[0]

In [23]:
print(row["chinese"])

14.分娩


In [24]:
print(row["english"])

Childbirth


In [25]:
output = row["Qwen/Qwen2-7B-Instruct/rpp-1.30"]
print(row["Qwen/Qwen2-7B-Instruct/rpp-1.30"])
detect_repetitions(output, debug=True)

Title: Birth

Translation:

Birth is a fundamental life event that marks the transition from dependency on another organism (usually through parental care) for survival to independence as part of human society's reproductive cycle.

The process typically involves several key stages:
- **Fertilization**: The fusion of sperm with egg cells inside or outside the female body leads to conception.
  
  - This can occur naturally during sexual intercourse when both partners contribute their gametes towards fertilizing each other’s eggs/ sperms respectively leading to pregnancy formation within about two weeks after ovulation if conditions allow successful implantation onto endometrial lining post-fertilisation phase where it then begins growing until birth occurs usually around nine months later due primarily biological reasons related to gestational development needed by fetus before delivery possible without significant harm inflicted upon either mother nor baby involved thereby ensuring he

(6, 42, 48)